
# Plot thermodynamic properties of H₂ vs. temperatures.

This example shows how to compute and plot the mass enthalpy of a plasma of hydrogen (H₂) as a
function of temperature.
It also shows how to compute and plot the mole fractions of the main species in the plasma
as a function of temperature, as well as the density and heat capacity.


The data for the mass enthalpy, density and heat capacity are compared to reference data from the literature.


## Equilibrium composition
The following species are considered in the mechanism:

- H, H2
- corresponding ions,
- electrons,

Data comes from the following sources:

- [GRCDatabase]_ for H, H2, H+ and H2+, and for electrons,

The thermo data are given as NASA 9 polynomial coefficients (For details, see
https://cantera.org/stable/reference/thermo/species-thermo.html#the-nasa-9-coefficient-polynomial-parameterization).

The temperature range is from 200 to 20000 K for atomic species, and from 200 to 6000 K for molecular species.

Then, to compute the equilibrium composition of the plasma, the Gibbs free energy minimization method is used.


## References data
The reference data for the mass enthalpy and density of hydrogen at 1 atm are taken from:

- [Boulos2023]_ for the mass enthalpy, density and heat capacity.
- [MinPlasCalc]_ (& [minplascalcPaper]_) for the mass enthalpy, density and heat capacity.
- [GRCDatabase]_ and [Burcat]_ for the mass enthalpy, density, heat capacity and equilibrium composition.


.. tags:: thermo, hydrogen, H2, plasma, mass enthalpy, density, heat capacity, ions, electrons


## Import the required libraries.



In [ ]:
import cantera as ct
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns

from rizer.io.thermo_transport_data_reader import ThermoTransportDataReader
from rizer.misc.utils import get_path_to_data

# Set the style of the plots.
sns.set_theme("talk")

## Define the thermo data files to load.



In [ ]:
mechanism = get_path_to_data("mechanisms", "Goutier2025", "CH4_to_C2H2.yaml")

# Load the gas phase.
gas = ct.Solution(
    mechanism,
    name="gas",
    transport_model=None,
)

## Define the temperature range.



In [ ]:
temperatures = np.linspace(300, 20000, 1000)

## Compute the mass enthalpy.



In [ ]:
states = ct.SolutionArray(gas)


for i, T in enumerate(temperatures):
    gas.TPX = T, ct.one_atm, "H2:1"
    gas.equilibrate("TP")
    states.append(gas.state)

## Load reference data.



In [ ]:
data_H2_Boulos2023 = ThermoTransportDataReader(
    gas_name="H2", pressure_atm=1, source="Boulos2023"
)
data_H2_minplascalc = ThermoTransportDataReader(
    gas_name="H2", pressure_atm=1, source="minplascalc"
)

## Plot the mass enthalpy vs. temperature.



In [ ]:
fig, ax = data_H2_Boulos2023.plot(
    x="T",
    y="h",
    show=False,
    label="Boulos2023",
    ls="-",
    lw=4,
    color="black",
)
data_H2_minplascalc.plot(
    x="T",
    y="h",
    fig_ax=(fig, ax),
    show=False,
    label="MinPlasCalc",
    ls="--",
    lw=3,
    color="red",
)
ax.plot(
    temperatures,
    states.enthalpy_mass,
    label="GRC+Burcat",
    lw=2,
    color="blue",
)
ax.legend()


plt.show()

## Plot the density vs. temperature.



In [ ]:
fig, ax = data_H2_Boulos2023.plot(
    x="T",
    y="rho",
    show=False,
    label="Boulos2023",
    ls="-",
    lw=4,
    color="black",
)
data_H2_minplascalc.plot(
    x="T",
    y="rho",
    fig_ax=(fig, ax),
    show=False,
    label="MinPlasCalc",
    ls="--",
    lw=3,
    color="red",
)
ax.plot(
    temperatures,
    states.density_mass,
    label="GRC+Burcat",
    lw=2,
    color="blue",
)
ax.legend()
ax.set_yscale("log")

plt.show()

## Plot the heat capacity vs. temperature.

We see some differences between the reference data and the computed data.
The difference is probably due to "total" heat capacity in the reference data,
while the computed data is the "non-reactive" heat capacity.



In [ ]:
fig, ax = data_H2_Boulos2023.plot(
    x="T",
    y="cp",
    show=False,
    label="Boulos2023",
    ls="-",
    lw=4,
    color="black",
)
data_H2_minplascalc.plot(
    x="T",
    y="cp",
    fig_ax=(fig, ax),
    show=False,
    label="MinPlasCalc",
    ls="--",
    lw=3,
    color="red",
)
ax.plot(
    temperatures,
    states.cp_mass,
    label="GRC+Burcat",
    lw=2,
    color="blue",
)
ax.legend()
ax.set_yscale("log")

plt.show()

## Plot mole fractions vs. temperature.



In [ ]:
main_species = ["H2", "H2+", "H", "H+", "e-"]
nice_names = {
    "H2": r"$\mathrm{H}_2$",
    "H2+": r"$\mathrm{H}_2^+$",
    "H": r"$\mathrm{H}$",
    "H+": r"$\mathrm{H}^+$",
    "e-": r"$\mathrm{e}^-$",
}

fig, ax = plt.subplots(figsize=(10, 6))


for species in main_species:
    ax.plot(temperatures, states(species).X * 100, label=species)

    # Annotate the maximum mole fraction, with the same color as the line.
    x_max = temperatures[np.argmax(states(species).X)]
    y_max = np.max(states(species).X) * 100
    color = plt.gca().lines[-1].get_color()
    ax.text(
        x_max,
        y_max,
        nice_names[species],
        horizontalalignment="center",
        verticalalignment="bottom",
        color=color,
        fontsize=20,
    )

ax.set_xlabel("Temperature [K]")
ax.set_ylabel("Mole fraction [%]")
ax.set_title(
    "Mole fractions of species at LTE at 1 atm for hydrogen vs Temperature.\n"
    "(Data from GRC+Burcat)"
)
plt.show()